In [1]:
import folium
import matplotlib
import numpy as np
from matplotlib.pyplot import imread
from matplotlib.colors import Normalize
from matplotlib.colors import ListedColormap
from folium import raster_layers

In [2]:
image = '/notebooks/resources/gpm/gpm_1d.20190531.tif'

In [3]:
from osgeo import gdal,ogr,osr

def GetExtent(gt,cols,rows):
    ''' Return list of corner coordinates from a geotransform

        @type gt:   C{tuple/list}
        @param gt: geotransform
        @type cols:   C{int}
        @param cols: number of columns in the dataset
        @type rows:   C{int}
        @param rows: number of rows in the dataset
        @rtype:    C{[float,...,float]}
        @return:   coordinates of each corner
    '''
    ext=[]
    xarr=[0,cols]
    yarr=[0,rows]

    for px in xarr:
        for py in yarr:
            x=gt[0]+(px*gt[1])+(py*gt[2])
            y=gt[3]+(px*gt[4])+(py*gt[5])
            ext.append([y,x])
            print (y,x)
        yarr.reverse()
    return ext

def ReprojectCoords(coords,src_srs,tgt_srs):
    ''' Reproject a list of x,y coordinates.

        @type geom:     C{tuple/list}
        @param geom:    List of [[x,y],...[x,y]] coordinates
        @type src_srs:  C{osr.SpatialReference}
        @param src_srs: OSR SpatialReference object
        @type tgt_srs:  C{osr.SpatialReference}
        @param tgt_srs: OSR SpatialReference object
        @rtype:         C{tuple/list}
        @return:        List of transformed [[x,y],...[x,y]] coordinates
    '''
    trans_coords=[]
    transform = osr.CoordinateTransformation( src_srs, tgt_srs)
    for x,y in coords:
        x,y,z = transform.TransformPoint(x,y)
        trans_coords.append([x,y])
    return trans_coords

raster=image
ds=gdal.Open(raster)

gt=ds.GetGeoTransform()
cols = ds.RasterXSize
rows = ds.RasterYSize

ext=GetExtent(gt,cols,rows)
print("ext = " + str(ext))

src_srs=osr.SpatialReference()
src_srs.ImportFromWkt(ds.GetProjection())
# tgt_srs=osr.SpatialReference()
# tgt_srs.ImportFromEPSG(3857)
tgt_srs = src_srs.CloneGeogCS()

geo_ext=ReprojectCoords(ext,src_srs,tgt_srs)
print("geo_ext = " + str(geo_ext))

10.0 -180.0
-60.0 -180.0
-60.0 -30.0
10.0 -30.0
ext = [[10.0, -180.0], [-60.0, -180.0], [-60.0, -30.0], [10.0, -30.0]]
geo_ext = [[10.0, -180.0], [-60.0, -180.0], [-60.0, -30.0], [10.0, -30.0]]


In [13]:
# Choose colormap
cmap = matplotlib.cm.cool

# Get the colormap colors
my_cmap = cmap(np.arange(cmap.N))


# Set alpha
my_cmap[:,-1] = np.linspace(0, 1, cmap.N)

# Create new colormap
my_cmap = ListedColormap(my_cmap)

In [14]:
m = folium.Map(
      location = [-22, -114]
    , zoom_start = 2
    , control_scale = True 
    , tiles = 'Stamen Terrain'
)

data = matplotlib.pyplot.imread(image)

# Image bounds on the map in the form
# [[lat_min, lon_min], [lat_max, lon_max]]
m.add_child(raster_layers.ImageOverlay(
      data
    , opacity = 0.7
    , bounds = [ext[2], ext[0]]
    , mercator_project = True
    , colormap = my_cmap
)
           )


folium.Marker(
      ext[2]
    , popup = str(ext[2])
    , tooltip = str(ext[2])
).add_to(m)

folium.Marker(
      ext[0]
    , popup = str(ext[0])
    , tooltip = str(ext[0])
).add_to(m)

m